In [1]:
#先padding(part1-part5)->暫存jsonl(part6)->再存成numpy(part7)

In [2]:
import pandas as pd
import re
from shutil import copyfile
import numpy as np

In [3]:
df_read= pd.read_csv('94_news.csv')
df_read= df_read.dropna()
df_read=df_read.reset_index()
df_read= df_read[['category','context']]
df_read = df_read.sample(n=94, random_state=1)
df_read = df_read.reset_index()
df_read = df_read[['category','context']]
df_read.to_csv('94_news_shuffle.csv')
df_read = pd.read_csv('94_news_shuffle.csv')

In [4]:
# padding

#part1: split the sentences in each paragraphs.
for i in range( len(df_read['context']) ):
    df_read['context'][i] = df_read['context'][i].replace(" ","")
    df_read['context'][i] = df_read['context'][i].replace("→","")
    df_read['context'][i] = df_read['context'][i].replace("●","")
    df_read['context'][i] = df_read['context'][i].replace("▲","")
    df_read['context'][i] = df_read['context'][i].replace("◎","")
    df_read['context'][i] = df_read['context'][i].replace("","")
    df_read['context'][i] = df_read['context'][i].replace("","")
    df_read['context'][i] = df_read['context'][i].replace("★","")
    df_read['context'][i] = df_read['context'][i].replace("◆","")
    df_read['context'][i] = df_read['context'][i].replace("☆","")
    df_read['context'][i] = df_read['context'][i].replace("\n","")
    df_read['context'][i] = re.split(r'[，。?!,.;；]',df_read['context'][i])


/workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
/workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/ipykernel_launcher.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
/workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  impor

In [5]:
df_read_copy = df_read

In [6]:
#part2: do zero padding on words of each sentences no matter the number of it is smaller than 20 or not.
for i in range( len(df_read['context']) ):
    for j in range( len( df_read['context'][i]) ):
        s=''
        if len( df_read['context'][i][j] ) > 0:
            for k in range( len( df_read['context'][i][j] ) ):
                s+= df_read['context'][i][j][k]
        for k in range( 50 ):
            s+=' 0'
        df_read['context'][i][j] = s

In [7]:
#part3: do zero padding on paragraphs whose number of sentences are smaller than 30.
sen_30zero='0'+' 0'*19
for i in range( len(df_read['context']) ):
    if len( df_read['context'][i] ) < 30:
        l=[]
        for j in range( len( df_read['context'][i] ) ):
            l.append( df_read['context'][i][j] )
        for j in range( 30-len( df_read['context'][i] ) ):
            l.append( sen_30zero )
        df_read['context'][i] = l

/workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.


In [8]:
#part4: delete sentences over 30. 
for i in range( len(df_read['context']) ):
    if ( len(df_read['context'][i]) ) > 30:
        df_read['context'][i] = df_read['context'][i][0:30]

/workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [9]:
#test
print( len(df_read['context']) )
print( len(df_read['context'][2]) )
print( len(df_read['context'][20][16]) )

94
30
123


In [10]:
#part5: then use BERT to do word embedding.
#for i in range(len(df_read['context'])):
bert_filename = 'AAApple.txt'
for i in range(0,94):
    np_filename=str(i)
    bertfile =  open(bert_filename, "w")
    for j in range(30):
        bertfile.writelines(str(df_read['context'][i][j]))
        bertfile.writelines('\n')
    bertfile.close()
    
    !python ./extract_features.py \
        --input_file=./AAApple.txt \
        --output_file=./AAApple.jsonl \
        --vocab_file=./chinese_L-12_H-768_A-12/vocab.txt \
        --bert_config_file=./chinese_L-12_H-768_A-12/bert_config.json \
        --init_checkpoint=./chinese_L-12_H-768_A-12/bert_model.ckpt \
        --layers=-1 \
        --max_seq_length=20 \
        --batch_size=8
    
    #copyfile('AAApple.jsonl', output_filename)
    df = pd.read_json('AAApple.jsonl',lines=True, orient='records')
    a_sentence=[]
    para=[]
    for linex_index in range(30):
        a_sentence=[]
        for seq in range(20):
            a_sentence.append( df['features'][linex_index][seq]['layers'][0]['values'] )
        para.append(a_sentence)

    if len(np_filename) < 5:
        str0=''
        for w in range( 5-len(np_filename) ):
            str0+='0'
        np_filename=str0+np_filename
    np.save('embedding/'+np_filename+'.npy',para)
    

W0829 10:22:03.362653 140096907695872 deprecation_wrapper.py:119] From ./extract_features.py:419: The name tf.app.run is deprecated. Please use tf.compat.v1.app.run instead.

W0829 10:22:03.363301 140096907695872 deprecation_wrapper.py:119] From ./extract_features.py:344: The name tf.logging.set_verbosity is deprecated. Please use tf.compat.v1.logging.set_verbosity instead.

W0829 10:22:03.363440 140096907695872 deprecation_wrapper.py:119] From ./extract_features.py:344: The name tf.logging.INFO is deprecated. Please use tf.compat.v1.logging.INFO instead.

W0829 10:22:03.363607 140096907695872 deprecation_wrapper.py:119] From /workdir2/home/2019intern/94_news/bert/modeling.py:93: The name tf.gfile.GFile is deprecated. Please use tf.io.gfile.GFile instead.

W0829 10:22:04.342836 140096907695872 lazy_loader.py:50] 
The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-c

I0829 10:22:08.530966 140096907695872 extract_features.py:186] **** Trainable Variables ****
I0829 10:22:08.531566 140096907695872 extract_features.py:192]   name = bert/embeddings/word_embeddings:0, shape = (21128, 768), *INIT_FROM_CKPT*
I0829 10:22:08.531846 140096907695872 extract_features.py:192]   name = bert/embeddings/token_type_embeddings:0, shape = (2, 768), *INIT_FROM_CKPT*
I0829 10:22:08.531957 140096907695872 extract_features.py:192]   name = bert/embeddings/position_embeddings:0, shape = (512, 768), *INIT_FROM_CKPT*
I0829 10:22:08.532057 140096907695872 extract_features.py:192]   name = bert/embeddings/LayerNorm/beta:0, shape = (768,), *INIT_FROM_CKPT*
I0829 10:22:08.532149 140096907695872 extract_features.py:192]   name = bert/embeddings/LayerNorm/gamma:0, shape = (768,), *INIT_FROM_CKPT*
I0829 10:22:08.532248 140096907695872 extract_features.py:192]   name = bert/encoder/layer_0/attention/self/query/kernel:0, shape = (768, 768), *INIT_FROM_CKPT*
I0829 10:22:08.532348 140

W0829 10:22:08.716228 140096907695872 deprecation.py:323] From /workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/tensorflow/python/ops/array_ops.py:1354: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
I0829 10:22:09.073891 140096907695872 monitored_session.py:240] Graph was finalized.
2019-08-29 10:22:09.074483: I tensorflow/core/platform/cpu_feature_guard.cc:142] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2019-08-29 10:22:09.093766: I tensorflow/stream_executor/platform/default/dso_loader.cc:42] Successfully opened dynamic library libcuda.so.1
2019-08-29 10:22:09.375545: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x7265610 executing computations on platform CUDA. Devices:
2019-08-29 10:22:09.375597: I tensorflow/compil

W0829 10:22:16.638070 140119576409856 estimator.py:1984] Estimator's model_fn (<function model_fn_builder.<locals>.model_fn at 0x7f6f3e7b07b8>) includes params argument, but params are not passed to Estimator.
W0829 10:22:16.639771 140119576409856 estimator.py:1811] Using temporary folder as model directory: /tmp/tmpubsyeh6d
I0829 10:22:16.640518 140119576409856 estimator.py:209] Using config: {'_model_dir': '/tmp/tmpubsyeh6d', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': None, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_service': None, '_cluster_spec': <tensorflow.python.tr

W0829 10:22:20.578716 140119576409856 deprecation.py:323] From /workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/tensorflow/python/ops/array_ops.py:1354: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
I0829 10:22:20.996650 140119576409856 monitored_session.py:240] Graph was finalized.
2019-08-29 10:22:20.997467: I tensorflow/core/platform/cpu_feature_guard.cc:142] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2019-08-29 10:22:21.008481: I tensorflow/stream_executor/platform/default/dso_loader.cc:42] Successfully opened dynamic library libcuda.so.1
2019-08-29 10:22:21.247420: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x5b2c3e0 executing computations on platform CUDA. Devices:
2019-08-29 10:22:21.247475: I tensorflow/compil

...

W0829 10:40:18.753296 140458408236800 deprecation.py:323] From /workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/tensorflow/python/ops/array_ops.py:1354: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
I0829 10:40:19.195330 140458408236800 monitored_session.py:240] Graph was finalized.
2019-08-29 10:40:19.195861: I tensorflow/core/platform/cpu_feature_guard.cc:142] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2019-08-29 10:40:19.216483: I tensorflow/stream_executor/platform/default/dso_loader.cc:42] Successfully opened dynamic library libcuda.so.1
2019-08-29 10:40:19.456225: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x720c8e0 executing computations on platform CUDA. Devices:
2019-08-29 10:40:19.456288: I tensorflow/compil

W0829 10:40:26.695695 140008246933248 estimator.py:1984] Estimator's model_fn (<function model_fn_builder.<locals>.model_fn at 0x7f5552b437b8>) includes params argument, but params are not passed to Estimator.
W0829 10:40:26.697376 140008246933248 estimator.py:1811] Using temporary folder as model directory: /tmp/tmpeo3qjyb3
I0829 10:40:26.698068 140008246933248 estimator.py:209] Using config: {'_model_dir': '/tmp/tmpeo3qjyb3', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': None, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_service': None, '_cluster_spec': <tensorflow.python.tr

W0829 10:40:30.748463 140008246933248 deprecation.py:323] From /workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/tensorflow/python/ops/array_ops.py:1354: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
I0829 10:40:31.116331 140008246933248 monitored_session.py:240] Graph was finalized.
2019-08-29 10:40:31.116846: I tensorflow/core/platform/cpu_feature_guard.cc:142] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2019-08-29 10:40:31.136022: I tensorflow/stream_executor/platform/default/dso_loader.cc:42] Successfully opened dynamic library libcuda.so.1
2019-08-29 10:40:31.375286: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x761a5a0 executing computations on platform CUDA. Devices:
2019-08-29 10:40:31.375354: I tensorflow/compil

W0829 10:40:38.673280 140029564397312 estimator.py:1984] Estimator's model_fn (<function model_fn_builder.<locals>.model_fn at 0x7f5a4958b7b8>) includes params argument, but params are not passed to Estimator.
W0829 10:40:38.674934 140029564397312 estimator.py:1811] Using temporary folder as model directory: /tmp/tmpi987tlba
I0829 10:40:38.675710 140029564397312 estimator.py:209] Using config: {'_model_dir': '/tmp/tmpi987tlba', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': None, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_service': None, '_cluster_spec': <tensorflow.python.tr

W0829 10:40:42.693577 140029564397312 deprecation.py:323] From /workdir2/home/2019intern/python3.6.9-intern/lib/python3.6/site-packages/tensorflow/python/ops/array_ops.py:1354: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where
I0829 10:40:43.077377 140029564397312 monitored_session.py:240] Graph was finalized.
2019-08-29 10:40:43.077893: I tensorflow/core/platform/cpu_feature_guard.cc:142] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2019-08-29 10:40:43.095509: I tensorflow/stream_executor/platform/default/dso_loader.cc:42] Successfully opened dynamic library libcuda.so.1
2019-08-29 10:40:43.342294: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x7679380 executing computations on platform CUDA. Devices:
2019-08-29 10:40:43.342371: I tensorflow/compil

In [11]:
np25=np.load('./embedding/00025.npy')
np25[29][19]

array([ 5.012520e-01, -5.479600e-02,  3.114450e-01,  2.955500e-01,
        2.335110e-01, -2.007850e-01, -6.430650e-01,  1.033255e+00,
       -5.787020e-01,  4.008900e-02,  1.956200e-01,  2.623930e-01,
       -2.188820e-01, -3.124170e-01,  1.067600e+00,  4.729000e-02,
        3.581050e-01, -6.236700e-02, -3.918530e-01, -4.680320e-01,
        5.694730e-01, -1.548140e-01,  2.074030e-01, -3.879050e-01,
       -1.101460e-01,  6.232060e-01, -4.626080e-01,  7.649400e-02,
       -1.308030e+00,  2.696400e-02,  4.292560e-01, -4.845800e-01,
       -1.450320e-01,  4.959080e-01,  1.476710e-01, -1.386940e-01,
        1.026950e-01,  7.540000e-03, -4.923190e-01, -1.464625e+00,
       -3.626730e-01, -3.521190e-01, -1.235469e+00, -4.651390e-01,
        8.656000e-02, -4.220520e-01, -4.007650e-01, -3.550640e-01,
       -1.017123e+00,  6.736050e-01,  7.556630e-01,  5.009601e+00,
        2.868140e-01,  8.136620e-01, -7.451430e-01, -4.669500e-02,
        2.665320e-01,  9.942200e-02,  1.029052e+00, -1.402858e

In [12]:
np25[2]

array([[ 0.247199,  0.602898,  0.480475, ...,  0.09097 , -0.21714 ,
        -0.231507],
       [ 0.133666,  0.545938, -0.478419, ...,  0.281582, -0.949444,
        -0.158654],
       [ 0.72897 , -0.120637, -0.491127, ...,  0.424025, -0.732091,
        -0.034854],
       ...,
       [ 1.367989, -0.299459,  0.197389, ..., -0.213984,  0.030937,
         0.090342],
       [ 1.151782,  0.632235,  0.558443, ..., -0.746308, -0.479496,
        -0.91969 ],
       [ 0.128491,  1.010245,  1.001081, ..., -0.493668, -0.756632,
        -0.319271]])

In [13]:
#目前跳過的檔案:
#66,67